In [1]:
import numpy as np
import math
from scipy.io import arff
from bisect import bisect_left


In [2]:
#Counts the occurence of each class label in labels
def class_counter(labels, label_list):
    counter = {}
    for a in label_list:
        counter[a] = 0
    for label in labels:
        counter[label.decode()] += 1
    return counter

#compute entropy of given the dictionary counter (class, count) and the complete size of the set all
def compute_entropy(counter, all):
    entropy = 0.
    for c in counter.values():
        p = c / all
        if p != 0:
            entropy += - p * math.log(p, 2.)
    return entropy


def x2_statistics(counter_l, counter_r ,all_l, all_r):
    x2 = 0
    ges = all_l + all_r #150
    for c in counter_l:
        o_l = counter_l[c] #observed frequency
        o_r = counter_r[c]
        ges_c = o_l + o_r #number of samples with class c
        e_l = all_l/ges *ges_c  #expected frequency
        e_r = all_r/ges *ges_c
        x2 += ((o_l - e_l)**2 / e_l + (o_r - e_r)**2 / e_r)
    return x2      

In [3]:
#load data from file: meta contains attribute descriptions
#data is an array of record objects
data, meta = arff.loadarff("iris.arff")
#print(data)
print(meta)
#extract label columns
Y = data['class']
# select l attributes
l=2
# data set as n objects
n = len(Y)
print("n:", n)
# data set has d features
d = len(meta.names())-1
# list of all class labels
class_values = meta['class'][1]
print("class values: ",class_values)
# list of all attribute names
attribute_list = meta.names()[0:d]
print("attributes: ", attribute_list)

Dataset: iris
	sepallength's type is numeric
	sepalwidth's type is numeric
	petallength's type is numeric
	petalwidth's type is numeric
	class's type is nominal, range is ('Iris-setosa', 'Iris-versicolor', 'Iris-virginica')

n: 150
class values:  ('Iris-setosa', 'Iris-versicolor', 'Iris-virginica')
attributes:  ['sepallength', 'sepalwidth', 'petallength', 'petalwidth']


In [4]:
#compute entropy of the complete data set
counter_all = class_counter(Y, class_values)
print(counter_all)
entropy_all = compute_entropy(counter_all, n)
print('Entropy: %s'%entropy_all)

{'Iris-virginica': 50, 'Iris-versicolor': 50, 'Iris-setosa': 50}
Entropy: 1.584962500721156


In [5]:
#collect the in info gain for each feature
Z=np.zeros(d)
#determine info gain for each dimension
i = 0
for attr in attribute_list:
    print(attr)
    #extract the i th column and sort it
    X = data[attr]
    srt = np.argsort(X)
    X=X[srt]
    #apply the same order to Y and build pairs of value and column
    Y2=Y[srt]
    X2 = zip(X,Y2)
    #Find all split values based on changing labels
    last_x = next(X2)
    splits = []
    for x in X2:
        if x[1] != last_x[1]: #if different label => possible split
            splits.append(x[0])
        last_x = x
    #Compute the Information Gain for all splits and keep the best
    split_vals = sorted(list(set(splits)))
    bestinfogain = 0
    bestx2 = 0
    #last_index =-1
    best_splitval_IG = -1
    best_splitval_X2 = -1
    for split in split_vals:
        #print('Dim: %s, Split at %s'%(i,split))
        #split the data and count the quantity for each label in each partition
        split_index = bisect_left(X, split)
        #print("index:", split_index)
        #determine size of each partition
        all_l = float(split_index)
        all_r = float(n-(split_index))
        if all_l == 0 or all_r == 0: continue
        #print ('Split value: %s, Split index: %s'%(split, split_index))
        #count entries per class and then compute entropy
        counter_l = class_counter(Y2[0:split_index], class_values)
        counter_r = class_counter(Y2[split_index:n], class_values)
        #compute entropy on both sides of the split
        #compute left and right entropy
        x2 = x2_statistics(counter_l, counter_r, all_l, all_r)
        if (x2 > bestx2):
            bestx2 = x2
            best_splitval_X2 = split
        #print('X2 : %s'%x2)
        #compute the info gain
        entropy_l = compute_entropy(counter_l, all_l)
        entropy_r = compute_entropy(counter_r, all_r)        
        #print('l: %s r:%s'%(entropy_l ,entropy_r))
        infogain = entropy_all - (all_l/n*entropy_l + all_r/n*entropy_r)
        #keep the highest gain
        if (infogain > bestinfogain):
            bestinfogain = infogain
            best_splitval_IG = split
        #print ('Information Gain: %s'%infogain)
        #last_index = split_index
    #collect the info gain for each attribute
    print('Best X2: %s at %s'%(round(bestx2, 3), best_splitval_X2))
    print('Best IG: %s at %s'%(round(bestinfogain, 5), best_splitval_IG))
    Z[i]= bestx2
    i += 1
#determine order w.r.t. to the highest infogain
Z = list(zip(attribute_list , Z))
Z.sort(key=lambda item: item[1], reverse=True)
print("\nAttributes ordered by Information Gain:")
for attr in Z:
    print(attr[0], round(attr[1],2))

sepallength
Best X2: 102.492 at 5.5
Best IG: 0.55723 at 5.6
sepalwidth
Best X2: 54.167 at 3.4
Best IG: 0.26791 at 3.4
petallength
Best X2: 150.0 at 3.0
Best IG: 0.9183 at 3.0
petalwidth
Best X2: 150.0 at 1.0
Best IG: 0.9183 at 1.0

Attributes ordered by Information Gain:
petallength 150.0
petalwidth 150.0
sepallength 102.49
sepalwidth 54.17
